The following processes are applied to both filtered and unfiltered data:
1. Epochs of 2 seconds, with an overlap of 0.75 are extracted from the data.
2. Epochs are standardized.
3. Epochs that are bad (e.g. due to eye blinks) are removed.

This data for both datasets is saved as "semiclean"

Further processing is done to make the data (potentially) more suitable for classification.
4. ICA is run on the data to remove artifacts.
5. the data is recomposed from resulting components.

Four sets of data are saved as fif files, and as pandas dataframes.


In [75]:
#import 
import mne
import os
import glob
import pandas as pd
from mne.utils import ProgressBar
from mne.preprocessing import ICA
import matplotlib
import matplotlib.pyplot as plt
import numpy as np
matplotlib.use('Qt5Agg')
import pickle
from autoreject import get_rejection_threshold

In [6]:
files = glob.glob('dataset2/data/filtered-ref/*.fif')

In [113]:
files_unfiltered = glob.glob('dataset2/data/unfiltered-ref/*.fif')

In [112]:

def clean(files, filtertype):
    n_files = len(files)
    data_filtered = pd.DataFrame()
    data_semifiltered = pd.DataFrame()
    # Make filtered dataset
    print("Filtering {n} files".format(n=n_files))
    # Initialize a progress bar.
    progress = ProgressBar(n_files, mesg='Filtering')
    for file in files:
        raw = mne.io.read_raw_fif(file, preload=True, verbose='error')
        #create epochs
        events = mne.make_fixed_length_events(raw, id=1, duration=2, overlap=.75)
        raw.info['projs'] = []
        epochs = mne.Epochs(raw, events, tmin=0, tmax=2, baseline=(0, 0), detrend=1, reject_by_annotation=True, preload=True, verbose='error')
        reject = get_rejection_threshold(epochs, decim=1)
        reject['mag'] = 5e-12
        reject['grad'] = 4000e-13
        # standardize epochs
        X = epochs.get_data() # EEG signals (n_epochs, n_channels, n_times)
        y = epochs.events[:, 2] # class labels (n_epochs)
        epochs_std = mne.decoding.Scaler(epochs.info, scalings='mean').fit_transform(X, y)
        epochs_std = mne.EpochsArray(epochs_std, epochs.info, events=epochs.events)
        # reject bad epochs
        ar = AutoReject(verbose=True)
        epochs_clean = ar.fit_transform(epochs_std)
        
        # save epochs
        if not os.path.exists(f'dataset2/data/{filtertype}-semiclean'):
            os.makedirs(f'dataset2/data/{filtertype}-semiclean')
        epochs_clean.save(f'dataset2/data/{filtertype}-semiclean/{file.split("/")[-1]}')

        # save dataframe
        temp_df = epochs_clean.to_data_frame()
        temp_df['subject'] = f'{file.split("/")[-1][0:11]}'
        data_semifiltered = data_semifiltered.append(temp_df, ignore_index=True)

        # aapply ICA
        epochs_tmp = epochs_clean.copy()
        picks = mne.pick_types(epochs_tmp.info, eeg=True, eog=False, stim=False, exclude='bads')
        ica = mne.preprocessing.ICA(method="infomax", fit_params=dict(extended=True), random_state=1, n_components = 19)
        ica.fit(epochs_tmp, picks=picks, reject=reject)
        ica.apply(epochs_tmp)
        # save in folder

        if not os.path.exists(f'dataset2/data/{filtertype}-clean'):
            os.makedirs(f'dataset2/data/{filtertype}-clean')
        epochs_tmp.save(f'dataset2/data/{filtertype}-clean/{file.split("/")[-1]}')

        #save in dataframe
        temp_df = epochs_tmp.to_data_frame()
        temp_df['subject'] = f'{file.split("/")[-1][0:11]}'
        data_filtered = data_filtered.append(temp_df, ignore_index=True)
        progress.update_with_increment_value(1)
    
    #pickle data filtered
    with open(f'dataset2/data/{filtertype}_filtered_epoch.pkl', 'wb') as f:
        pickle.dump(data_filtered, f)
    #pickle data semifiltered
    with open(f'dataset2/data/{filtertype}_semifiltered_epoch.pkl', 'wb') as f:
        pickle.dump(data_filtered, f)

In [114]:
clean(files_unfiltered, 'unfiltered')

Filtering 384 files


  0%|          | Filtering : 0/384 [00:00<?,       ?it/s]/tmp/ipykernel_19693/691220900.py:13: DeprecationWarning: projs cannot be set directly. This warning will turn into an error after 0.24
  raw.info['projs'] = []


Estimating rejection dictionary for eeg
Not setting metadata
Not setting metadata
38 matching events found
No baseline correction applied
0 projection items activated
0 bad epochs dropped
Running autoreject on ch_type=eeg






















100%|██████████| Creating augmented epochs : 19/19 [00:00<00:00,   28.08it/s]




















100%|██████████| Computing thresholds ... : 19/19 [00:17<00:00,    1.10it/s]











100%|██████████| Repairing epochs : 38/38 [00:00<00:00,  200.49it/s]






































100%|██████████| Repairing epochs : 38/38 [00:00<00:00,   41.84it/s]






















100%|██████████| Fold : 10/10 [00:00<00:00,   21.05it/s]






































100%|██████████| Repairing epochs : 38/38 [00:00<00:00,   39.72it/s]






















100%|██████████| Fold : 10/10 [00:00<00:00,   26.38it/s]






































100%|██████████| Repairing epochs : 38/38 [00:00<00:00,   38.07it/s]








100%|██████████| Fold : 10/10 [00:00<00:00,  176.90it/s]
100%|██████████| n_interp : 3/3 [00:03<00:00,    1.31s/it]






Estimated consensus=1.00 and n_interpolate=18


...



















100%|██████████| Creating augmented epochs : 19/19 [00:00<00:00,   48.97it/s]




















100%|██████████| Computing thresholds ... : 19/19 [00:10<00:00,    1.84it/s]







100%|██████████| Repairing epochs : 38/38 [00:00<00:00,  346.24it/s]


























100%|██████████| Repairing epochs : 38/38 [00:00<00:00,   67.19it/s]






















100%|██████████| Fold : 10/10 [00:00<00:00,   32.95it/s]



































100%|██████████| Repairing epochs : 38/38 [00:00<00:00,   56.07it/s]






















100%|██████████| Fold : 10/10 [00:00<00:00,   39.52it/s]





































100%|██████████| Repairing epochs : 38/38 [00:00<00:00,   54.25it/s]




100%|██████████| Fold : 10/10 [00:00<00:00,  296.60it/s]
100%|██████████| n_interp : 3/3 [00:02<00:00,    1.13it/s]






Estimated consensus=1.00 and n_interpolate=18






































100%|██████████| Repairing epochs : 38/38 [00:00<00:00,   52.39it/s]


No bad epochs were found for your data. Returning a copy of the data you wanted to clean. Interpolation may have been done.
Fitting ICA to data using 19 channels (please be patient, this may take a while)
Selecting by number: 19 components
Computing Extended Infomax ICA
Fitting ICA took 8.6s.
Applying ICA to Epochs instance
    Transforming to ICA space (19 components)
    Zeroing out 0 ICA components
    Projecting back using 19 PCA components


100%|██████████| Filtering : 384/384 [3:06:23<00:00,   29.12s/it]


In [111]:
clean(files, 'filtered')

Filtering 384 files


Estimating rejection dictionary for eeg


/tmp/ipykernel_19693/1754095207.py:13: DeprecationWarning: projs cannot be set directly. This warning will turn into an error after 0.24
  raw.info['projs'] = []


Not setting metadata
Not setting metadata
38 matching events found
No baseline correction applied
0 projection items activated
0 bad epochs dropped
Running autoreject on ch_type=eeg










































100%|██████████| Creating augmented epochs : 19/19 [00:00<00:00,   41.65it/s]








































100%|██████████| Computing thresholds ... : 19/19 [00:16<00:00,    1.14it/s]










100%|██████████| Repairing epochs : 38/38 [00:00<00:00,  225.88it/s]



































100%|██████████| Repairing epochs : 38/38 [00:00<00:00,   45.03it/s]






















100%|██████████| Fold : 10/10 [00:00<00:00,   22.30it/s]



































100%|██████████| Repairing epochs : 38/38 [00:00<00:00,   45.17it/s]






















100%|██████████| Fold : 10/10 [00:00<00:00,   25.51it/s]



































100%|██████████| Repairing epochs : 38/38 [00:01<00:00,   33.92it/s]








100%|██████████| Fold : 10/10 [00:00<00:00,  177.54it/s]
100%|██████████| n_interp : 3/3 [00:03<00:00,    1.28s/it]


...

100%|██████████| Creating augmented epochs : 19/19 [00:00<00:00,   65.23it/s]
100%|██████████| Computing thresholds ... : 19/19 [00:09<00:00,    1.90it/s]







100%|██████████| Repairing epochs : 38/38 [00:00<00:00,  349.25it/s]





























100%|██████████| Repairing epochs : 38/38 [00:00<00:00,   62.76it/s]






















100%|██████████| Fold : 10/10 [00:00<00:00,   33.48it/s]































100%|██████████| Repairing epochs : 38/38 [00:00<00:00,   61.58it/s]






















100%|██████████| Fold : 10/10 [00:00<00:00,   39.29it/s]































100%|██████████| Repairing epochs : 38/38 [00:00<00:00,   62.41it/s]




100%|██████████| Fold : 10/10 [00:00<00:00,  319.12it/s]
100%|██████████| n_interp : 3/3 [00:02<00:00,    1.19it/s]






Estimated consensus=1.00 and n_interpolate=18


































100%|██████████| Repairing epochs : 38/38 [00:00<00:00,   60.82it/s]


No bad epochs were found for your data. Returning a copy of the data you wanted to clean. Interpolation may have been done.
Fitting ICA to data using 19 channels (please be patient, this may take a while)
Selecting by number: 19 components
Computing Extended Infomax ICA
Fitting ICA took 10.7s.
Applying ICA to Epochs instance
    Transforming to ICA space (19 components)
    Zeroing out 0 ICA components
    Projecting back using 19 PCA components



100%|██████████| Filtering : 384/384 [2:53:58<00:00,   27.18s/it]
